In [1]:
import os
import datetime

import re

import plotly.graph_objs as go
import plotly.tools as tls
import plotly.offline as plty
from plotly.tools import FigureFactory as ff
plty.init_notebook_mode(connected=True)
import cufflinks as cf
cf.go_offline()
cf.set_config_file(theme='white')

import statsmodels.api as sm

import matplotlib.pyplot as plt
%matplotlib inline

import pandas as pd
import numpy as np
import scipy

import collections

from sklearn import linear_model
from sklearn import preprocessing
from sklearn import metrics

import copy

from analysis_utils import utils


# Import data

In [2]:
home = os.path.expanduser('~')
data_dir = os.path.join(home, 'data_sets')
site_file = os.path.join(data_dir, 'site-info.csv')
sites_dict = {}
time_stamp = 'hourly'
for f in os.listdir(data_dir):
    if time_stamp not in f: continue
    digits = re.findall('\d+', f)
    sites_dict[int(digits[0])] = os.path.join(data_dir, f)

## Read site info

In [3]:
site_data = pd.read_csv(site_file)

## Read CSV files to make dataframe

In [4]:
systems_df = utils.read_csv_to_ts(sites_dict, 'array_performance_ratio')

site 1283 -- array_performance_ratio is empty
site 1292 -- array_performance_ratio is empty
site 1231 -- array_performance_ratio is empty
site 1424 -- array_performance_ratio is empty
site 1425 -- array_performance_ratio is empty
site 1236 -- array_performance_ratio is empty
site 1422 -- array_performance_ratio is empty
site 1239 -- array_performance_ratio is empty
site 1423 -- array_performance_ratio is empty
site 1389 -- array_performance_ratio is empty
site 1199 -- array_performance_ratio is empty
site 1332 -- array_performance_ratio is empty
site 1208 -- array_performance_ratio is empty
site 1405 -- array_performance_ratio is empty
site 1429 -- array_performance_ratio is empty


In [5]:
print(len(systems_df.keys()))

18


# Yearly trend

In [6]:
yearly = systems_df.resample('A').mean()
yearly = yearly[yearly.index < '2017']

In [7]:
yearly.iplot()

In [8]:
yearly.describe()

2         1284      1289       10        1229      1230      18    \
count  6.000000  4.000000  5.000000  11.000000  7.000000  6.000000  7.000000   
mean   0.588866  0.898664  0.700837   0.801334  0.598528  0.700893  0.759353   
std    0.058915  0.037793  0.009390   0.038455  0.062910  0.045953  0.020374   
min    0.478172  0.848872  0.690688   0.742899  0.497132  0.658011  0.720487   
25%    0.581560  0.886723  0.698572   0.766577  0.574567  0.666525  0.753224   
50%    0.605317  0.902628  0.698580   0.799178  0.592530  0.685668  0.760657   
75%    0.629363  0.914570  0.700052   0.829947  0.626321  0.728854  0.773054   
max    0.633370  0.940529  0.716292   0.851556  0.698261  0.772616  0.781769   

           1277       4         3         33        34        35         39    \
count  6.000000  10.000000  6.000000  7.000000  7.000000  7.000000   8.000000   
mean   0.617973   0.789422  0.587984  0.769538  0.679324  0.574553   4.436718   
std    0.011650   0.071112  0.181956  0.022003  0.022618  0.013677   6.130285   
min    0.599705   0.676456  0.229845  0.735232  0.653526  0.549764   0.887062   
25%    0.612052   0.750732  0.591163  0.763440  0.656274  0.571325   1.027839   
50%    0.619233   0.804644  0.679682  0.764414  0.692435  0.572253   2.189136   
75%    0.627007   0.841505  0.686666  0.776442  0.697666  0.581723   4.461790   
max    0.630412   0.873304  0.688046  0.807354  0.701426  0.593758  19.119396   

           1207     1403      1276      1278  
count  2.000000  1.00000  6.000000  6.000000  
mean   0.823285  0.83717  0.541678  0.571456  
std    0.014968      NaN  0.006910  0.022774  
min    0.812700  0.83717  0.531985  0.540765  
25%    0.817992  0.83717  0.538114  0.555141  
50%    0.823285  0.83717  0.540696  0.577847  
75%    0.828577  0.83717  0.547176  0.582681  
max    0.833869  0.83717  0.550100  0.600412

In [9]:
regression_info, fits = utils.linear_fit_ts(yearly)
regression_info.T['coefficient'] *= 365

In [10]:
print(regression_info)

                 2         3         4         10        18        33    \
coefficient -0.016049 -0.043953  0.011826  0.008029 -0.003003  0.000469   
intercept    0.631699  0.705292  0.736158  0.761159  0.768369  0.768129   
r_sq         0.346913  0.272789  0.253867  0.480212  0.101548  0.002124   

                 34        35        39        1207      1229      1230  \
coefficient -0.009458  0.002298 -0.750478  0.021111 -0.022709 -0.011642   
intercept    0.707721  0.567653  7.441456  0.812700  0.666709  0.730019   
r_sq         0.817352  0.131976  0.128624  1.000000  0.609046  0.224922   

                 1276      1277      1278      1284      1289     1403  
coefficient  0.003621  0.004853 -0.007037 -0.018602 -0.002065  0.00000  
intercept    0.532616  0.605827  0.589067  0.926567  0.704968  0.83717  
r_sq         0.962394  0.608313  0.334662  0.403769  0.121005  1.00000  


In [11]:
pct_deg = utils.calc_pct_deg(regression_info)

In [12]:
pct_deg

2       -2.540580
3       -6.231864
4        1.606418
10       1.054845
18      -0.390839
33       0.061071
34      -1.336451
35       0.404855
39     -10.085092
1207     2.597609
1229    -3.406147
1230    -1.594748
1276     0.679795
1277     0.801075
1278    -1.194541
1284    -2.007610
1289    -0.292887
1403     0.000000
dtype: float64

In [13]:
pct_deg.describe()

count    18.000000
mean     -1.215283
std       3.007391
min     -10.085092
25%      -1.904394
50%      -0.341863
75%       0.611060
max       2.597609
dtype: float64

In [14]:
pct_deg.iplot(kind='hist', bins=30)

# Performance ratio by month

In [24]:
daily = systems_df.resample('D').mean()

In [25]:
daily.iplot()

In [26]:
titles = tuple(['system_id: ' + str(i) for i in sorted(daily.keys())])

cols = 1
rows = len(titles) // cols

months = {
    1: 'J',
    2: 'F',
    3: 'M',
    4: 'A',
    5: 'M',
    6: 'J',
    7: 'J',
    8: 'A',
    9: 'S',
    10: 'O',
    11: 'N',
    12: 'D'
}

print(rows, cols)

fig = tls.make_subplots(rows=rows, cols=cols, subplot_titles=titles)
for i, site, in enumerate(sorted(daily.keys())):
    this_site = daily[site].dropna()
    traces = []
    for month, month_group in this_site.groupby(this_site.index.month):
        #print(site, month, month_group)
        #print(month_group.values)
        traces.append(go.Box(x=month, y=month_group.values, name=month, boxpoints='all'))
        # traces.append(go.Scatter(x=[month for i in range(len(month_group.values))], y=month_group.values))
    for trace in traces:
        fig.append_trace(trace, i % rows + 1, i // rows + 1)

fig['layout'].update(height=4000, width=600, showlegend=False)
for i in range(1, len(titles) + 1):
    fig['layout']['yaxis' + str(i)].update(range=[0, 1.1])
    fig['layout']['xaxis' + str(i)].update(tickmode='array', 
                                           tickvals=[i for i in range(1, 13)],
                                           ticktext=[months[i] for i in range(1, 13)])

plty.iplot(fig)

18 1
This is the format of your plot grid:
[ (1,1) x1,y1 ]   
[ (2,1) x2,y2 ]   
[ (3,1) x3,y3 ]   
[ (4,1) x4,y4 ]   
[ (5,1) x5,y5 ]   
[ (6,1) x6,y6 ]   
[ (7,1) x7,y7 ]   
[ (8,1) x8,y8 ]   
[ (9,1) x9,y9 ]   
[ (10,1) x10,y10 ]
[ (11,1) x11,y11 ]
[ (12,1) x12,y12 ]
[ (13,1) x13,y13 ]
[ (14,1) x14,y14 ]
[ (15,1) x15,y15 ]
[ (16,1) x16,y16 ]
[ (17,1) x17,y17 ]
[ (18,1) x18,y18 ]

